In [1]:
import pandas as pd
import altair as alt

data = pd.read_csv("./Databases/compiled_db.csv")
data.head()

Unnamed: 0                                    Title Release Date  \
0           0                               Elden Ring    25-Feb-22   
1           1                                    Hades    10-Dec-19   
2           2  The Legend of Zelda: Breath of the Wild     3-Mar-17   
3           3                                Undertale    15-Sep-15   
4           4                            Hollow Knight    24-Feb-17   

                                                Team  Rating Times Listed  \
0     ['Bandai Namco Entertainment', 'FromSoftware']     4.5         3.9K   
1                               ['Supergiant Games']     4.3         2.9K   
2  ['Nintendo', 'Nintendo EPD Production Group No...     4.4         4.3K   
3                                 ['tobyfox', '8-4']     4.2         3.5K   
4                                    ['Team Cherry']     4.4           3K   

   Number of Reviews                                             Genres  \
0               3900                               ['Adventure', 'RPG']   
1               2900           ['Adventure', 'Brawler', 'Indie', 'RPG']   
2               4300                               ['Adventure', 'RPG']   
3               3500  ['Adventure', 'Indie', 'RPG', 'Turn Based Stra...   
4               3000                 ['Adventure', 'Indie', 'Platform']   

   Plays Playing  ...                   Publisher Year Released  \
0  17000    3.8K  ...  Bandai Namco Entertainment          2022   
1  21000    3.2K  ...                         NaN          2019   
2  30000    2.5K  ...                    Nintendo          2017   
3  28000     679  ...                    Toby Fox          2015   
4  21000    2.4K  ...                 Team Cherry          2017   

  Month Released Game Type    Genre 1  Genre 2   Genre 3              Genre 4  \
0            Feb       AAA  Adventure      RPG       NaN                  NaN   
1            Dec     Indie  Adventure  Brawler     Indie                  RPG   
2            Mar       AAA  Adventure      RPG       NaN                  NaN   
3            Sep     Indie  Adventure    Indie       RPG  Turn Based Strategy   
4            Feb     Indie  Adventure    Indie  Platform                  NaN   

  Genre 5 Genre 6  
0     NaN     NaN  
1     NaN     NaN  
2     NaN     NaN  
3     NaN     NaN  
4     NaN     NaN  

[5 rows x 23 columns]

In [2]:
# Implementing Overview+Detail using semantic zoom
year_selection = alt.selection_point(fields=["Year Released"])
base = alt.Chart(data).properties(width=800, height=250)

#Specify our overview chart
overview = alt.Chart(data).mark_bar().encode(
    x = alt.X("Year Released").scale(zero=False),
    y = alt.Y("mean(Rating)"),
    color = alt.condition(year_selection, alt.value("orange"), alt.value("lightgrey"))
).add_params(year_selection).properties(width=400, height=250)

# Specify our detail chart
detail = base.mark_bar().encode(
    y = "mean(Rating)",    
    x = "Title",
    color = alt.condition(alt.FieldEqualPredicate(field="Game Type", equal="Indie"), alt.value("blue"), alt.value("red")),
    tooltip=["Title", "Rating", "Year Released"]
).transform_filter(year_selection).properties(width=800, height=250)

overview | detail

alt.HConcatChart(...)

In [3]:
# Implement genre filtering
genre_list = ['', 'Adventure', 'RPG', 'Indie', 'Turn Based Strategy', 'Platform', 'Simulator', 'Brawler', 'Puzzle', 'Shooter', 'Music', 'Strategy', 
              'Fighting', 'Visual Novel', 'Tactical', 'Racing', 'Arcade', 'Point-and-Click', 'Sport', 'Card & Board Game', 'Real Time Strategy']
genre_dropdown = alt.binding_select(options=genre_list, name="Select a genre to filter (empty selection to see all games): ")
genre_selector = alt.param(name='SelectorName', value='', bind=genre_dropdown)

alt.Chart(data).mark_circle().encode(
    x = alt.X("Release Date:T"),
    y = "Rating",
    color = alt.condition(alt.FieldEqualPredicate(field="Game Type", equal="Indie"), alt.value("blue"), alt.value("red")),
    size = alt.Size('Plays', scale=alt.Scale(domain=[-5000, 100000])),
    tooltip=["Title", "Rating", "Year Released"],
    opacity=alt.condition(
        alt.expr.test(alt.expr.regexp(genre_selector, 'i'), alt.datum.Genres), 
        alt.value(1), 
        alt.value(.05))
).properties(width=800, height=500).add_params(genre_selector).interactive()

alt.Chart(...)

In [4]:
# Uses only Genre 1 as the 'main genre' for selection
genre_list = ['Adventure', 'RPG', 'Indie', 'Turn Based Strategy', 'Platform', 'Simulator', 'Brawler', 'Puzzle', 'Shooter', 'Music', 'Strategy', 
              'Fighting', 'Visual Novel', 'Tactical', 'Racing', 'Arcade', 'Point-and-Click', 'Sport', 'Card & Board Game', 'Real Time Strategy']
genre_dropdown = alt.binding_select(options=genre_list, name="Select a genre to filter: ")

selection = alt.selection_point(fields=["Genre 1"], bind=genre_dropdown)

color = alt.condition(
    selection,
    alt.Color('Genre 1:N', scale=alt.Scale(scheme='category20')),
    alt.value('lightgray')
)
alt.Chart(data).mark_circle().encode(
    x = alt.X("Release Date:T"),
    y = "Rating",
    color=color,
    # TODO: maybe add something to make size bigger if game is indie, or maybe change shape if that's an option?
    tooltip=["Title", "Rating", "Year Released"],
    opacity=alt.condition(selection,alt.value(1),alt.value(.1)),
).add_params(selection).properties(width=800, height=500).interactive()



alt.Chart(...)

In [5]:
# Comparing genres, Indie vs. AAA
dropdown = alt.binding_select(options=["Indie", "AAA"], name="Select a type to filter: ")

selection = alt.selection_point(fields=["Game Type"], bind=dropdown)

color = alt.condition(
    selection,
    alt.Color('Genre 1:N', scale=alt.Scale(scheme='category20')),
    alt.value('lightgray')
)
alt.Chart(data).mark_circle().encode(
    x = alt.X("Release Date:T"),
    y = "Rating",
    color=color,
    tooltip=["Title", "Rating", "Year Released"],
    opacity=alt.condition(selection,alt.value(1),alt.value(.1)),
).add_params(selection).properties(width=800, height=500).interactive()



alt.Chart(...)

In [6]:
# Two kinds of filtering? NOT WORKING YET, maybe this one doesn't even really matter since we already are using colors

# Implement genre filtering
genre_list = ['', 'Adventure', 'RPG', 'Indie', 'Turn Based Strategy', 'Platform', 'Simulator', 'Brawler', 'Puzzle', 'Shooter', 'Music', 'Strategy', 
              'Fighting', 'Visual Novel', 'Tactical', 'Racing', 'Arcade', 'Point-and-Click', 'Sport', 'Card & Board Game', 'Real Time Strategy']
genre_dropdown = alt.binding_select(options=genre_list, name="Select a genre to filter by (empty selection to see all games): ")
genre_selector = alt.param(name='GenreSelector', value='', bind=genre_dropdown)

# Implement indie vs. AAA filtering
game_type_list = ['', 'AAA', 'Indie']
game_type_dropdown = alt.binding_select(options=game_type_list, name="Select a game type to filter by (empty selection to see all games): ")
game_type_selector = alt.param(name='GameTypeSelector', value='', bind=game_type_dropdown)
game_type = "Game Type"

alt.Chart(data).mark_circle().encode(
    x = alt.X("Release Date:T"),
    y = "Rating",
    color = alt.condition(alt.FieldEqualPredicate(field="Game Type", equal="Indie"), alt.value("blue"), alt.value("red")),
    # size = "Plays", # don't implement size until we have more reliable data on sales
    tooltip=["Title", "Rating", "Year Released"],
    opacity=alt.condition(
        alt.expr.test(alt.expr.regexp(genre_selector, 'i'), alt.datum.Genres) & alt.expr.test(alt.expr.regexp(game_type_selector, 'i'), alt.datum.game_type), 
        alt.value(1), 
        alt.value(.05))
).properties(width=800, height=500).add_params(genre_selector, game_type_selector).interactive()

alt.Chart(...)

In [7]:
# Create a "success" timeline for number of reviews
genre_list = ['', 'Adventure', 'RPG', 'Indie', 'Turn Based Strategy', 'Platform', 'Simulator', 'Brawler', 'Puzzle', 'Shooter', 'Music', 'Strategy', 
              'Fighting', 'Visual Novel', 'Tactical', 'Racing', 'Arcade', 'Point-and-Click', 'Sport', 'Card & Board Game', 'Real Time Strategy']
genre_dropdown = alt.binding_select(options=genre_list, name="Select a genre to filter (empty selection to see all games): ")
genre_selector = alt.param(name='SelectorName', value='', bind=genre_dropdown)

alt.Chart(data).mark_circle().encode(
    x = alt.X("Release Date:T"),
    y = "Number of Reviews",
    color = alt.condition(alt.FieldEqualPredicate(field="Game Type", equal="Indie"), alt.value("blue"), alt.value("red")),
    tooltip=["Title", "Rating", "Year Released"],
    opacity=alt.condition(
        alt.expr.test(alt.expr.regexp(genre_selector, 'i'), alt.datum.Genres), 
        alt.value(1), 
        alt.value(.05))
).properties(width=800, height=500).add_params(genre_selector).interactive()

alt.Chart(...)

In [8]:
# Create a "success" timeline for number of plays
genre_list = ['', 'Adventure', 'RPG', 'Indie', 'Turn Based Strategy', 'Platform', 'Simulator', 'Brawler', 'Puzzle', 'Shooter', 'Music', 'Strategy', 
              'Fighting', 'Visual Novel', 'Tactical', 'Racing', 'Arcade', 'Point-and-Click', 'Sport', 'Card & Board Game', 'Real Time Strategy']
genre_dropdown = alt.binding_select(options=genre_list, name="Select a genre to filter (empty selection to see all games): ")
genre_selector = alt.param(name='SelectorName', value='', bind=genre_dropdown)

alt.Chart(data).mark_circle().encode(
    x = alt.X("Release Date:T"),
    y = "Plays",
    color = alt.condition(alt.FieldEqualPredicate(field="Game Type", equal="Indie"), alt.value("blue"), alt.value("red")),
    tooltip=["Title", "Rating", "Year Released"],
    opacity=alt.condition(
        alt.expr.test(alt.expr.regexp(genre_selector, 'i'), alt.datum.Genres), 
        alt.value(1), 
        alt.value(.05))
).properties(width=800, height=500).add_params(genre_selector).interactive()

alt.Chart(...)